#  Analyze EGFD Accountability Data 

E.Quinn  7/28/2018

In [28]:
import re
import numpy as np
import scipy as sc
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
import struct
from datetime import datetime
import datetime

In [29]:
pd.set_option('display.max_rows', 3000)

## Dictionary for looking up name by page

In [30]:
FF_name = {1: 'FF Andrade', 2: 'FF Archambault', 3: 'Lt Babcock', 4: 'Lt Bailey', 5: 'Lt Beaudreau', \
    6: 'FF Campbell', 7: 'FF Columbier', 8: 'Prob-FF Crute', 9: 'FF DeLuca', 10: 'FF Forte', \
    11: 'Lt Gardner', 12: 'Prob-FF Gorman', 13: 'Lt Grady', 14: 'Lt Greene', \
    15: 'Lt Hall', 16: 'FF Howard', 17: 'Lt Jones', 18: 'FF King', 19: 'FF Lang Jr.', 20: 'Prob-FF Lavallee', \
    21: 'FF Marsh', 22: 'Lt Matola, Jr.', 23: 'FF McKeon', 24: 'Capt Mears', 25: 'Lt Monaghan', \
    26: 'Capt Montville', 27: "FF O'Donnell", 28: 'Prob-FF Perry', 29: 'Lt Perry', 30: 'Prob-FF Preston', \
    31: 'Lt Purcell', 32: 'Lt Richardson', 33: 'FF Snowling', 34: 'FF Stabile', 35: 'FF Szerlag', 36: 'Lt Warner III'}                 

## Dictionary for looking up page by name

In [31]:
FF_ID = {'FF Andrade': 1,'FF Archambault': 2,'Lt Babcock': 3,'Lt Bailey': 4,'Lt Beaudreau': 5,'FF Campbell': 6, \
         'FF Columbier': 7,'Prob-FF Crute': 8,'FF DeLuca': 9,'FF Forte': 10,'Lt Gardner': 11,'Prob-FF Gorman': 12, \
         'Lt Grady': 13,'Lt Greene': 14,'Lt Hall': 15,'FF Howard': 16,'Lt Jones': 17,'FF King': 18,'FF Lang Jr.': 19, \
         'Prob-FF Lavallee': 20,'FF Marsh': 21,'Lt Matola, Jr.': 22,'FF McKeon': 23,'Capt Mears': 24,'Lt Monaghan': 25, \
         'Capt Montville': 26,"FF O'Donnell": 27,'Prob-FF Perry': 28,'Lt Perry': 29,'Prob-FF Preston': 30,  \
         'Lt Purcell': 31,'Lt Richardson': 32,'FF Snowling': 33,'FF Stabile': 34,'FF Szerlag': 35,'Lt Warner III': 36}                 


## Dictionary of short names

In [32]:
FF_short_name = {1: 'FF DA', 2: 'FF SA', 3: 'Lt SB', 4: 'Lt TB', 5: 'Lt RB', 6: 'FF AC', \
         7: 'FF MC', 8: 'PFF SC', 9: 'FF AD', 10: 'FF SF', 11: 'Lt RG', 12: 'PFF DG', 13: 'Lt RG', 14: 'Lt MG',  \
         15: 'Lt KH', 16: 'FF MH', 17: 'Lt MJ', 18: 'FF KK', 19: 'FF KL', 20: 'PFF DL', 21: 'FF WM', \
         22: 'Lt EM', 23: 'FF SM', 24: 'Cpt TM', 25: 'Lt MM', 26: 'Cpt KM', 27: 'FF PO', 28: 'PFF JP',  \
         29: 'Lt BP', 30: 'PFF RP', 31: 'Lt WP', 32: 'Lt JR', 33: 'FF GS', 34: 'FF BS', 35: 'FF JS', 36: 'Lt RW'}                 


## Dictionary of initials by Page Number

In [33]:
FF_initials = {1: 'DA', 2: 'SA', 3: 'SB', 4: 'TB', 5: 'RB', 6: 'AC', 7: 'MC', 8: 'SC', 9: 'AD', 10: 'SF', 11: 'RG',  \
         12: 'DG', 13: 'RG', 14: 'MG', 15: 'KH', 16: 'MH', 17: 'MJ', 18: 'KK', 19: 'KL', 20: 'DL', 21: 'WM', \
         22: 'EM', 23: 'SM', 24: 'TM', 25: 'MM', 26: 'KM', 27: 'PO', 28: 'JP', 29: 'WP', 30: 'RP', 31: 'WP', \
         32: 'JR', 33: 'GS', 34: 'BS', 35: 'JS', 36: 'RW'}                 


## Dictionary for looking up platoon by name

In [34]:
FF_platoon = {'FF Andrade': 'C','FF Archambault': 'A','Lt Babcock': 'D','Lt Bailey': 'A','Lt Beaudreau': 'B','FF Campbell': 'A', \
         'FF Columbier': 'B','Prob-FF Crute': 'B','FF DeLuca': 'A','FF Forte': 'C','Lt Gardner': 'B','Prob-FF Gorman': 'D', \
         'Lt Grady': 'B','Lt Greene': 'B','Lt Hall': 'D','FF Howard': 'B','Lt Jones': 'C','FF King': 'C','FF Lang Jr.': 'D', \
         'Prob-FF Lavallee': 'D','FF Marsh': 'D','Lt Matola, Jr.': 'D','FF McKeon': 'C','Capt Mears': 'C','Lt Monaghan': 'A', \
         'Capt Montville': 'A',"FF O'Donnell": 'A','Prob-FF Perry': 'B','Lt Perry': 'B','Prob-FF Preston': 'A',  \
         'Lt Purcell': 'C','Lt Richardson': 'A','FF Snowling': 'B','FF Stabile': 'D','FF Szerlag': 'C','Lt Warner III': 'D'}                 


## Dictionary for looking up identifier by name

In [35]:
FF_token = {'FF Andrade': 'CFF2','FF Archambault': 'AFF1','Lt Babcock': 'DOF2','Lt Bailey': 'AOF2', \
        'Lt Beaudreau': 'BOF3','FF Campbell': 'AFF4', \
        'FF Columbier': 'BFF1','Prob-FF Crute': 'BFF4','FF DeLuca': 'AFF5','FF Forte': 'CFF4', \
        'Lt Gardner': 'BOF2','Prob-FF Gorman': 'DFF5', \
        'Lt Grady': 'BOF4','Lt Greene': 'COF4','Lt Hall': 'DOF1','FF Howard': 'BFF3','Lt Jones': 'COF2', \
        'FF King': 'CFF1','FF Lang Jr.': 'DFF3', \
        'Prob-FF Lavallee': 'DFF4','FF Marsh': 'DFF1','Lt Matola, Jr.': 'DOF4','FF McKeon': 'CFF5', \
        'Capt Mears': 'COF1','Lt Monaghan': 'AOF4', \
        'Capt Montville': 'AOF3',"FF O'Donnell": 'AFF2','Prob-FF Perry': 'BFF5','Lt Perry': 'BOF1', \
        'Prob-FF Preston': 'AFF3', 'Lt Purcell': 'COF3','Lt Richardson': 'AOF1','FF Snowling': 'BFF2', \
        'FF Stabile': 'DFF2','FF Szerlag': 'CFF3','Lt Warner III': 'DOF3','FF Squillante':'EFF1'}                 


## Dictionary for looking up name by identifier

In [36]:
token_FF = {'CFF2':'FF Andrade','AFF1':'FF Archambault','DOF2':'Lt Babcock','AOF2':'Lt Bailey', \
        'BOF3':'Lt Beaudreau','AFF4':'FF Campbell', \
        'BFF1':'FF Columbier','BFF4':'Prob-FF Crute','AFF5':'FF DeLuca','CFF4':'FF Forte', \
        'BOF2':'Lt Gardner','DFF5':'Prob-FF Gorman', \
        'BOF4':'Lt Grady','COF4':'Lt Greene','DOF1':'Lt Hall','BFF3':'FF Howard','COF2':'Lt Jones', \
        'CFF1':'FF King','DFF3':'FF Lang Jr.', \
        'DFF4':'Prob-FF Lavallee','DFF1':'FF Marsh','DOF4':'Lt Matola, Jr.','CFF5':'FF McKeon', \
        'COF1':'Capt Mears','AOF4':'Lt Monaghan', \
        'AOF3':'Capt Montville','AFF2':"FF O'Donnell",'BFF5':'Prob-FF Perry','BOF1':'Lt Perry', \
        'AFF3':'Prob-FF Preston', 'COF3':'Lt Purcell','AOF1':'Lt Richardson','BFF2':'FF Snowling', \
        'DFF2':'FF Stabile','CFF3':'FF Szerlag','DOF3':'Lt Warner III','EFF1':'FF Squillante'}                 


## Dictionary of 8-day cycle start times by platoon

In [37]:
base_date = {}
base_date['A'] = datetime.datetime(2016,12,26,7,0,0)   #first cycle start 1/1/2017 07:00 or earlier for this platoon
base_date['B'] = datetime.datetime(2016,12,28,7,0,0)
base_date['C'] = datetime.datetime(2016,12,30,7,0,0)
base_date['D'] = datetime.datetime(2017,1,1,7,0,0)

cycle_start = {}                                       # dictionary for cycle start by platoon

max_datetime = datetime.datetime(2018,7,1,0,0,0)

for platoon in base_date.keys():                      # loop through earliest cycle start for each platoon
    cycle_start[platoon] = {}                         # create dictionary for platoon
    ss = base_date[platoon]                           # start with earliest cycle start time
    while (ss < max_datetime):                         # loop until cycle start is past max_datetime
        cycle_start[platoon][ss] = {}                 # add dictionary for cycle start
        ss += datetime.timedelta(days=8)               # increment cycle start by 8 days

cycle_start

print('Number of 8-Day Cycles')
print('A ' + str(len(cycle_start['A'])))
print('B ' + str(len(cycle_start['B'])))
print('C ' + str(len(cycle_start['C'])))
print('D ' + str(len(cycle_start['D'])))

Number of 8-Day Cycles
A 69
B 69
C 69
D 69


In [38]:
base_date

{'A': datetime.datetime(2016, 12, 26, 7, 0),
 'B': datetime.datetime(2016, 12, 28, 7, 0),
 'C': datetime.datetime(2016, 12, 30, 7, 0),
 'D': datetime.datetime(2017, 1, 1, 7, 0)}

## Build list of shifts for each FF

In [39]:
shifts = {}       

for platoon in ['A','B','C','D']:
    for ffn in ['OF1','OF2','OF3','OF4','FF1','FF2','FF3','FF4','FF5']:
        token = platoon+ ffn
        shifts[token] = {}
        shifts[token]['name'] = token_FF[token]
        shifts[token]['platoon'] = platoon
        shifts[token]['shifts'] = {}
        for cycle in cycle_start[platoon]:
            shift = cycle
            shifts[token]['shifts'][shift] = {'type':'scheduled'}
            shift += datetime.timedelta(days=1)   # increment cycle start by 10 hours + 1 day
            shifts[token]['shifts'][shift] = {'type':'scheduled'}
            shift += datetime.timedelta(days=1)
            shift += datetime.timedelta(hours=10)   # increment cycle start by 10 hours + 1 day
            shifts[token]['shifts'][shift] = {'type':'scheduled'}
            shift += datetime.timedelta(days=1)   # increment cycle start by 1 day
            shifts[token]['shifts'][shift] = {'type':'scheduled'}
        

## Lookup dictionary to get accountability file names by FF

These are the .csv files extracted from Eric's spreadsheet of accountability data

In [40]:
logs = {'FF Andrade': 'FF_Andrade.csv', \
                       'FF Archambault': 'FF_Archambault.csv', \
                       'Lt Babcock': 'Lt_Babcock.csv', \
                       'Lt Bailey': 'Lt_Bailey.csv', \
                       'Lt Beaudreau': 'Lt_Beaudreau.csv', \
                       'FF Campbell': 'FF_Campbell.csv', \
                       'FF Columbier': 'FF_Columbier.csv', \
                       'Prob-FF Crute': 'Prob-FF_Crute.csv', \
                       'FF DeLuca': 'FF_DeLuca.csv', \
                       'FF Forte': 'FF_Forte.csv', \
                       'Lt Gardner': 'Lt_Gardner.csv', \
                       'Prob-FF Gorman': 'Prob-FF_Gorman.csv', \
                       'Lt Grady': 'Lt_Grady.csv', \
                       'Lt Greene': 'Lt_Greene.csv', \
                       'Lt Hall': 'FF_Hall.csv', \
                       'FF Howard': 'FF_Howard.csv', \
                       'Lt Jones': 'Lt_Jones.csv', \
                       'FF King': 'FF_King.csv',
                       'FF Lang Jr.': 'FF_Lang.csv', \
                       'Prob-FF Lavallee': 'Prob-FF_Lavallee.csv', \
                       'FF Marsh': 'FF_Marsh.csv', \
                       'Lt Matola, Jr.': 'Lt_Matola.csv', \
                       'FF McKeon': 'FF_McKeon.csv', \
                       'Capt Mears': 'Capt_Mears.csv', \
                       'Lt Monaghan': 'Lt_Monaghan.csv', \
                       'Capt Montville': 'Capt_Montville.csv', \
                       "FF O'Donnell": 'FF_ODonnell.csv', \
                       'Prob-FF Perry': 'Prob-FF_Perry.csv', \
                       'Lt Perry': 'Lt_Perry.csv', \
                       'Prob-FF Preston': 'Prob-FF_Preston.csv',  \
                       'Lt Purcell': 'Lt_Purcell.csv', \
                       'Lt Richardson': 'Lt_Richardson.csv', \
                       'FF Snowling': 'FF_Snowling.csv', \
                       'FF Stabile': 'FF_Stabile.csv', \
                       'FF Szerlag': 'FF_Szerlag.csv', \
                       'Lt Warner III': 'Lt_Warner.csv'}                 

## Read the accountability logs and add the data to the dictionaries

There is one .csv file containing the accountability data for each firefighter

Data elements are added to the dictionary for that firefighter and shift

In [41]:
def findOccurrences(s, ch):
    return [i for i, letter in enumerate(s) if letter == ch]

In [42]:
def clean_reason(reason,for_ff):
    new_reason = ''
    if (for_ff == ''):
        new_reason += reason
    else:
        if ((',' in reason) & ('-' in reason)):
            ix = findOccurrences(reason,'-')
            ix_last = ix[len(ix)-1]
            new_reason += FF_token[for_ff] + reason[ix_last:]

    return(new_reason)        

In [43]:
def read_acct(token):
    
    ff_name = token_FF[token]
    fname = '../' + logs[ff_name]                                   #get the filename for this FF
    acctdf = pd.read_csv(fname,parse_dates=[[0,1]],skiprows=2,header=None)   #read it
    acctdf.rename(columns={'0_1': 'shift',2:'type',3:'hours',4:'rank',5:'reason'},inplace=True)
    acctdf['FF_name'] = ff_name       #create a column for this FFs name
    
    for index, row in acctdf.iterrows():    #loop through row by row and add data to dictionary
        ff_name = row['FF_name']             #shifts dictionary key is FF name
        shift = row['shift'].to_pydatetime()
        dtv = datetime.datetime(shift.year,shift.month,shift.day,shift.hour,0,0)
        if dtv not in shifts[token]['shifts']:
            shifts[token]['shifts'][dtv] = {}
        
        try:                                      #create dictionary for accountability data
            sdict = shifts[token]['shifts'][dtv]['acct']
        except KeyError:                          #if this shift was not found add it
            shifts[token]['shifts'][dtv]['acct'] = {}
            sdict = shifts[token]['shifts'][dtv]['acct']
                                                  #fill in the accountability data elements
        typ = row['type']
        sdict['type'] = row['type']
        sdict['hours'] = float(row['hours'])
        sdict['rank'] = row['rank']
        sdict['reason'] = row['reason']
        rstr = row['reason']                      #determine whose shift was being covered
        for_ff = ''                               #search for specific name in reason string
        if isinstance(rstr, str):
            if ('Andrade' in rstr):  for_ff = 'FF Andrade'
            if ('Archambault' in rstr):  for_ff = 'FF Archambault'
            if ('Babcock' in rstr):  for_ff = 'Lt Babcock'
            if ('Bailey' in rstr): for_ff = 'Lt Bailey'
            if ('Beaudreau' in rstr): for_ff = 'Lt Beaudreau'
            if ('Campbell' in rstr): for_ff = 'FF Campbell'
            if ('Columbier' in rstr): for_ff = 'FF Columbier'
            if ('Crute' in rstr): for_ff = 'Prob-FF Crute'
            if ('DeLuca' in rstr): for_ff = 'FF DeLuca'
            if ('Forte' in rstr): for_ff = 'FF Forte'
            if ('Gardner' in rstr): for_ff = 'Lt Gardner'
            if ('Gorman' in rstr): for_ff = 'Prob-FF Gorman'
            if ('Grady' in rstr): for_ff = 'Lt Grady'
            if ('Greene' in rstr): for_ff = 'Lt Greene'
            if ('Hall' in rstr): for_ff = 'Lt Hall'
            if ('Howard' in rstr): for_ff = 'FF Howard'
            if ('Jones' in rstr): for_ff = 'Lt Jones'
            if ('King' in rstr): for_ff = 'FF King'
            if ('Lang' in rstr): for_ff = 'FF Lang Jr.'
            if ('Lavallee' in rstr): for_ff = 'Prob-FF Lavallee'
            if ('Marsh' in rstr): for_ff = 'FF Marsh'
            if ('Matola' in rstr): for_ff = 'Lt Matola, Jr.'
            if ('McKeon' in rstr): for_ff = 'FF McKeon'
            if ('Mears' in rstr): for_ff = 'Capt Mears'
            if ('Monaghan' in rstr): for_ff = 'Lt Monaghan'
            if ('Montville' in rstr): for_ff = 'Capt Montville'
            if ('Donnell' in rstr): for_ff = "FF O'Donnell"
            if ('FF Perry' in rstr): for_ff = 'Prob-FF Perry'
            if ('Lt Perry' in rstr): for_ff = 'Lt Perry'
            if ('Preston' in rstr): for_ff = 'Prob-FF Preston'
            if ('Purcell' in rstr): for_ff = 'Lt Purcell'
            if ('Richardson' in rstr): for_ff = 'Lt Richardson'
            if ('Snowling' in rstr): for_ff = 'FF Snowling'
            if ('Squillante' in rstr): for_ff = 'FF Squillante'
            if ('Stabile' in rstr): for_ff = 'FF Stabile'
            if ('Szerlag' in rstr): for_ff = 'FF Szerlag'
            if ('Warner' in rstr): for_ff = 'Lt Warner III'
            if (len(for_ff) > 0):
                shifts[token]['shifts'][dtv]['acct']['for_token'] = FF_token[for_ff]    #save FF being covered
            else:
                shifts[token]['shifts'][dtv]['acct']['for_token'] = ''  #no for_ff
            shifts[token]['shifts'][dtv]['acct']['clean_reason'] = clean_reason(rstr,for_ff)
    return()

In [44]:
for token in shifts.keys():
    read_acct(token)

In [45]:
#shifts['AOF1']

## Write web page displaying results

In [46]:
def cellcolor(token,ts,shifts):
    bgcolor = '#FFFFFF'
    try:
        typ = shifts[token]['shifts'][ts]['acct']['type']
        if (typ == 'VC'): bgcolor = '#C0C0C0'
        if (typ == 'IOD'): bgcolor = '#FF00FF'
        if (typ in ['PRS','BER']): bgcolor = '#FFFF00'
        if ('CS-' in typ): bgcolor = '#00FF00'
        if ('C-' in typ): bgcolor = '#00FF00'
    except KeyError:
        x=1
    return(bgcolor)

In [47]:
def line2(token,ts,shifts):
    l2str = '<br>'
    try:
        typ = shifts[token]['shifts'][ts]['acct']['type']
        tag = token + str(ts)
        if (typ in ['VC','IOD','SWAP','SWAPW','SL','PRS','BER']): 
            l2str += '<a href="#' + tag + '">' + typ + '</a>'
        if ('OT-' in typ): l2str += '<a href="#' + tag + '">' + typ + '</a>'
        if (('C-' in typ) | ('CS-' in typ)): l2str += '<a href="#' + tag + '">' + typ + '</a>'
    except KeyError:
        ;
    return(l2str)

In [48]:
def line3(token,ts,shifts):
    l3str = '<br>'
    
    try:
        if (shifts[token]['shifts'][ts]['acct']['for_token'] != ''):
            token2 = shifts[token]['shifts'][ts]['acct']['for_token']
            tag = token2 + str(ts)
            l3str += '<a href="#' + tag + '">' + token2 + '</a>'
        else:
            for token2 in shifts.keys():
                try:
                    if (shifts[token2]['shifts'][ts]['acct']['for_token'] == token):
                        tag = token2 + str(ts)
                        l3str += '<a href="#' + tag + '">' + token2 + '</a>'
                except KeyError:
                    ;

    except KeyError:
            ;
    return(l3str)

In [49]:
def shiftabl(token,year,month,hour,shifts,file):        
    ndays = {1:31,2:28,3:31,4:30,5:31,6:30,7:31,8:31,9:30,10:31,11:30,12:31}
    if (hour == 7): 
        full_shift=10
        rowstr = '<tr align="center"><td rowspan="2">' + str(month) + '/' + str(year) + '</td>'
        rowstr +='<td>07:00</td>'
    else: 
        full_shift=14
        rowstr = '<tr><td>17:00</td>'
    
    for d in range(1,1+ndays[month]):
        ts = datetime.datetime(year,month,d,hour,0,0)
        tag = token + str(ts)
        
        rowstr += '<td bgcolor="' + cellcolor(token,ts,shifts) + '">'
        
                                                        #see if we are scheduled this shift
        try:
            if (shifts[token]['shifts'][ts]['type']=='scheduled'):   #see if there is an entry for this timestamp
                rowstr += 'On'
        except KeyError:
            rowstr += '&nbsp;'
        rowstr += line2(token,ts,shifts)
        rowstr += line3(token,ts,shifts)
        rowstr += '</td>'
    file.write(rowstr + '</tr>\n')
    return()

In [50]:
file = open('../test_V2.html','w') 

file.write('<html><body>') 

for token in shifts.keys():
    ff_name = token_FF[token]
    file.write('<a name="' + ff_name + '">')
    file.write('<h2>' + token + ' ' + '</h2></a>\n')
    file.write('<table border="1">\n')
    
    file.write('<tr><td>Month</td><td>Shift</td>')
    for d in range(1,32):
        file.write('<td>' + str(d) + '</td>')
    file.write('</tr>\n')
    
    year = 2017
    month = 1
    
    for i in range(1,18):
            
        shiftabl(token,year,month,7,shifts,file)  
        shiftabl(token,year,month,17,shifts,file) 
        
        month += 1
        if (month > 12):
            year += 1
            month = 1
        
    file.write('</table>\n')
    
for token in shifts.keys():
    ff_name = token_FF[token]
    file.write('<a name="acct_' + token + '">\n')
    file.write('<h2>' + token + ' ' + '</h2></a>\n')
    file.write('<table border="1">\n')
    file.write('<tr><td>Shift</td><td>Type</td><td>Hours</td><td>Rank</td><td>Reason</td></tr>\n')

    for shift in shifts[token]['shifts'].keys():
        sdict = shifts[token]['shifts'][shift]
        try:
            entry_type = sdict['acct']['type']
            hours = sdict['acct']['hours']
            rank = sdict['acct']['rank']
            reason = sdict['acct']['clean_reason']
            tag = token + str(shift)
            file.write('<tr><td><a name="' + tag + '"></a>' + str(shift) + '</td>')
            file.write('<td>' + entry_type + '</td>')
            file.write('<td>' + str(hours) + '</td>')
            file.write('<td>' + rank + '</td>')
            file.write('<td>' + str(reason) + '</td></tr>\n')
        except KeyError:
            continue
    file.write('</table>\n')

file.close() 

In [51]:
tot_hrs = {}

for token in shifts.keys():
    tot_hrs[token] = {}
    tot_hrs[token]['scheduled_hours'] = 0.0
    for shift in shifts[token]['shifts']:
        if (shift.hour == 7): shift_hours = 10.0
        if (shift.hour == 17): shift_hours = 14.0

        if ('type' in shifts[token]['shifts'][shift].keys()):
            typ = shifts[token]['shifts'][shift]['type']
            if (typ == 'scheduled'): tot_hrs[token]['scheduled_hours'] += shift_hours
        if ('acct' in shifts[token]['shifts'][shift].keys()):
            typ = shifts[token]['shifts'][shift]['acct']['type']
            if (typ in tot_hrs[token].keys()):
                tot_hrs[token][typ] += shifts[token]['shifts'][shift]['acct']['hours']
            else:
                tot_hrs[token][typ] = shifts[token]['shifts'][shift]['acct']['hours']
                    

In [52]:
def scheduled_this_cycle(cs):            #returns the four shifts scheduled in this cycle
    
    ts_list = []
    ts = cs
    ts_list.append(ts)
    ts += datetime.timedelta(days=1)
    ts_list.append(ts)
    ts += datetime.timedelta(days=1)
    ts += datetime.timedelta(hours=10)   # increment cycle start by 10 hours + 1 day
    ts_list.append(ts)
    ts += datetime.timedelta(days=1)
    ts_list.append(ts)
    return(ts_list)

In [53]:
def this_cycle(cs):            #returns the 16 shifts scheduled in this 8-day cycle
    
    cy_list = []
    ts = cs
    for hrs in [0,10,14,10,14,10,14,10,14,10,14,10,14,10,14,10]:
        ts += datetime.timedelta(hours=hrs)
        cy_list.append(ts)
    print(cy_list)
    return(cy_list)

In [54]:
def shift_hours(token,ts,shifts):            #returns a dictionary with all hours for this cycle
    
    sh = {}
    
    try:
        this_ff = shifts[token]['shifts'][ts]   #see if they have a record for this shift
        if ('acct' in this_ff.keys()):
            typ = this_ff['acct']['type']
            sh[typ] = this_ff['acct']['hours']
        if ('type' in this_ff.keys()):
            typ = this_ff['type']
            if (ts.hour == 7): sh[typ] = 10.0
            if (ts.hour == 17): sh[typ] = 14.0
    except KeyError:
            ;
    return(sh)
            

In [55]:
def full_shift(ts):
    if (ts.hour == 7): hours = 10.0
    if (ts.hour == 17): hours = 14.0
    return(hours)

In [56]:
def disp_val(typ,dct):
    disp_val = '&nbsp'
    if (typ in dct.keys()):
        if (dct[typ] > 0.0): disp_val = str(dct[typ])
    return(disp_val)

In [57]:
def add_hours(dct,key,x):
    if (key in dct.keys()):
        dct[key] += x
    else:
        dct[key] = x
    return()

In [58]:
def add_cumulative_hours(dct,totdct):
    for key in dct.keys():
        if (key in totdct.keys()):
            totdct[key] += dct[key]
        else:
            totdct[key] = dct[key]
    return()

In [59]:
def write_column_headings(file):
    file.write('<table border="1" width="100%">')
    file.write('<tr><td>FF</td>')
    file.write('<td>Scheduled</td>')
    file.write('<td>Regular</td>')
    file.write('<td>VC</td>')
    file.write('<td>SL</td>')
    file.write('<td>IOD</td>')
    file.write('<td>SWAP</td>')
    file.write('<td>CD</td>')
    file.write('<td>OT</td>')
    file.write('<td>OT-VAC</td>')
    file.write('<td>OT-SL</td>')
    file.write('<td>OT-IOD</td>')
    file.write('</tr>\n')
    return()

In [60]:
def write_cycle_row(token,cycle_hours,file):
    file.write('<tr><td>' + token + '</td>')
    file.write('<td>' + disp_val('scheduled',cycle_hours) + '</td>')
    file.write('<td>' + disp_val('reg_hours',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('VC',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('SL',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('IOD',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('SWAP',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('C-DD',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('OT',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('OT-VC',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('OT-SL',cycle_hours) +'</td>')
    file.write('<td>' + disp_val('OT_IOD',cycle_hours) +'</td>')
    file.write('</tr></td>')
    return()

In [61]:
file = open('../summary.html','w') 

file.write('<html><body>') 

file.write('<table border="1" width="80%">')

total_hours = {}

cycle_count = 0

for platoon in ['A','B','C','D']:
    
    for cs in cycle_start[platoon].keys():
        cycle_count += 1
        file.write('<tr><td>')
        file.write('<table border="1" width="100%"><tr><td>Platoon</td><td>Cycle Start</td></tr>')
        file.write('<tr><td>' + platoon + '</td><td>' + str(cs) + '</td></tr></table>\n')
        full_cycle = this_cycle(cs)
        print(cs)
        print('new cycle***********************************')
        write_column_headings(file)
        for ffn in ['OF1','OF2','OF3','OF4','FF1','FF2','FF3','FF4','FF5']:
            token = platoon+ ffn
            print(token)
            cycle_hours = {}                            #hours for this FF in this 8-day cycle
            for ts in full_cycle:
                try:
                    ds = shifts[token]['shifts'][ts]
                    print(ts)
                    print(ds)
                    try:                                  #if this FF was scheduled, show full shift scheduled
                        typ = ds['type']
                        if (typ == 'scheduled'):      #if this is the only entry FF worked full shift
                            add_hours(cycle_hours,'scheduled',full_shift(ts))
                    except KeyError:
                        ;
                    if ('acct' not in ds.keys()):      #if this is the only entry FF worked full shift
                            add_hours(cycle_hours,'reg_hours',full_shift(ts))
                    try:
                        typ = ds['acct']['type']
                        add_hours(cycle_hours,typ,ds['acct']['hours'])
                    except KeyError:
                        ;

                except KeyError:
                    ;
                print(ts)
                print(cycle_hours)
            write_cycle_row(token,cycle_hours,file)
            add_cumulative_hours(cycle_hours,total_hours)

        file.write('</table></td></tr>')
        file.write('\n')

total_hours['cycle_count'] = cycle_count

print(total_hours)

file.write('<tr><td><table border="1" width="100%">')
file.write('<tr><td>ALL</td>')
file.write('<td>8-Day Cycles</td>')
file.write('<td>Scheduled</td>')
file.write('<td>Regular</td>')
file.write('<td>VC</td>')
file.write('<td>SL</td>')
file.write('<td>IOD</td>')
file.write('<td>SWAP</td>')
file.write('<td>CD</td>')
file.write('<td>OT</td>')
file.write('<td>OT-VAC</td>')
file.write('<td>OT-SL</td>')
file.write('<td>OT-IOD</td>')
file.write('</tr>')
file.write('<tr><td>Totals</td>')
file.write('<td>' + disp_val('cycle_count',total_hours) + '</td>')
file.write('<td>' + disp_val('scheduled',total_hours) + '</td>')
file.write('<td>' + disp_val('reg_hours',total_hours) +'</td>')
file.write('<td>' + disp_val('VC',total_hours) +'</td>')
file.write('<td>' + disp_val('SL',total_hours) +'</td>')
file.write('<td>' + disp_val('IOD',total_hours) +'</td>')
file.write('<td>' + disp_val('SWAP',total_hours) +'</td>')
file.write('<td>' + disp_val('C-DD',total_hours) +'</td>')
file.write('<td>' + disp_val('OT',total_hours) +'</td>')
file.write('<td>' + disp_val('OT-VC',total_hours) +'</td>')
file.write('<td>' + disp_val('OT-SL',total_hours) +'</td>')
file.write('<td>' + disp_val('OT_IOD',total_hours) +'</td>')
file.write('</tr></td>')
file.write('</table></td></tr>')
file.write('</table>')
file.write('\n')

        

[datetime.datetime(2016, 12, 26, 7, 0), datetime.datetime(2016, 12, 26, 17, 0), datetime.datetime(2016, 12, 27, 7, 0), datetime.datetime(2016, 12, 27, 17, 0), datetime.datetime(2016, 12, 28, 7, 0), datetime.datetime(2016, 12, 28, 17, 0), datetime.datetime(2016, 12, 29, 7, 0), datetime.datetime(2016, 12, 29, 17, 0), datetime.datetime(2016, 12, 30, 7, 0), datetime.datetime(2016, 12, 30, 17, 0), datetime.datetime(2016, 12, 31, 7, 0), datetime.datetime(2016, 12, 31, 17, 0), datetime.datetime(2017, 1, 1, 7, 0), datetime.datetime(2017, 1, 1, 17, 0), datetime.datetime(2017, 1, 2, 7, 0), datetime.datetime(2017, 1, 2, 17, 0)]
2016-12-26 07:00:00
new cycle***********************************
AOF1
2016-12-26 07:00:00
{'type': 'scheduled'}
2016-12-26 07:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2016-12-26 17:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2016-12-27 07:00:00
{'type': 'scheduled'}
2016-12-27 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2016-12-27 17:00:00
{'scheduled': 20.0, 'reg

{'scheduled': 48.0, 'reg_hours': 48.0}
2017-02-01 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-02-01 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-02-02 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-02-02 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-02-03 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-02-03 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
AFF5
2017-01-27 07:00:00
{'type': 'scheduled'}
2017-01-27 07:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2017-01-27 17:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2017-01-28 07:00:00
{'type': 'scheduled'}
2017-01-28 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2017-01-28 17:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2017-01-29 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2017-01-29 17:00:00
{'type': 'scheduled'}
2017-01-29 17:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2017-01-30 07:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2017-01-30 17:00:00
{'type': 'scheduled'}
2017-01-30 17:00:00
{

2017-03-11 07:00:00
{'scheduled': 34.0, 'reg_hours': 34.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-11 17:00:00
{'type': 'scheduled'}
2017-03-11 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-12 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-12 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-13 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-13 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-14 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-14 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-15 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
2017-03-15 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT': 1.5, 'SWAPW': 5.0}
AFF1
2017-03-08 07:00:00
{'type': 'scheduled'}
2017-03-08 07:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2017-03-08 1

{'scheduled': 20.0, 'reg_hours': 20.0}
2017-04-11 17:00:00
{'type': 'scheduled'}
2017-04-11 17:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2017-04-12 07:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2017-04-12 17:00:00
{'type': 'scheduled'}
2017-04-12 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-13 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-13 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-14 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-14 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-15 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-15 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-16 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2017-04-16 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
[datetime.datetime(2017, 4, 17, 7, 0), datetime.datetime(2017, 4, 17, 17, 0), datetime.datetime(2017, 4, 18, 7, 0), datetime.datetime(2017, 4, 18, 17, 0), datetime.datetime(2017, 4, 19, 7, 0), datetime.datetime(2017, 4, 19, 17, 

{'scheduled': 48.0, 'reg_hours': 48.0, 'SWAPW': 14.0, 'OT-VC': 10.0}
2017-06-03 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'SWAPW': 14.0, 'OT-VC': 10.0}
AOF2
2017-05-27 07:00:00
{'type': 'scheduled'}
2017-05-27 07:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2017-05-27 17:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2017-05-28 07:00:00
{'type': 'scheduled'}
2017-05-28 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2017-05-28 17:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2017-05-29 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2017-05-29 17:00:00
{'type': 'scheduled'}
2017-05-29 17:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2017-05-30 07:00:00
{'acct': {'type': 'OT-COMP', 'hours': 10.0, 'rank': 'Lt', 'reason': 'Lt Grady, Ryan - Comp USED', 'for_token': 'BOF4', 'clean_reason': 'BOF4- Comp USED'}}
2017-05-30 07:00:00
{'scheduled': 34.0, 'reg_hours': 34.0, 'OT-COMP': 10.0}
2017-05-30 17:00:00
{'type': 'scheduled'}
2017-05-30 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0, 'OT-C

...

{'type': 'scheduled'}
2018-01-30 17:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2018-01-31 07:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2018-01-31 17:00:00
{'type': 'scheduled', 'acct': {'type': 'SL', 'hours': 14.0, 'rank': 'FF', 'reason': 'Sick', 'for_token': '', 'clean_reason': 'Sick'}}
2018-01-31 17:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-01 07:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-01 17:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-02 07:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-02 17:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-03 07:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-03 17:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-04 07:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
2018-02-04 17:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'SL': 14.0}
DFF4
2018-01-28 07:00:00
{'type': 'scheduled'}
2018-01-28 07:00:00


2018-03-12 17:00:00
{'type': 'scheduled'}
2018-03-12 17:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-13 07:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-13 17:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-14 07:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-14 17:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-15 07:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-15 17:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-16 07:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
2018-03-16 17:00:00
{'scheduled': 48.0, 'reg_hours': 38.0, 'SWAP': 10.0}
DFF4
2018-03-09 07:00:00
{'type': 'scheduled'}
2018-03-09 07:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2018-03-09 17:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2018-03-10 07:00:00
{'type': 'scheduled'}
2018-03-10 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2018-03-10 17:00:00
{'scheduled': 2

2018-04-18 07:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2018-04-18 17:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2018-04-19 07:00:00
{'type': 'scheduled'}
2018-04-19 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2018-04-19 17:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2018-04-20 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2018-04-20 17:00:00
{'type': 'scheduled'}
2018-04-20 17:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2018-04-21 07:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2018-04-21 17:00:00
{'type': 'scheduled', 'acct': {'type': 'ACT', 'hours': 14.0, 'rank': 'FF', 'reason': nan}}
2018-04-21 17:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'ACT': 14.0}
2018-04-22 07:00:00
{'acct': {'type': 'OT-SL', 'hours': 10.0, 'rank': 'FF', 'reason': 'FF Howard, Matthew (D) - Sick', 'for_token': 'BFF3', 'clean_reason': 'BFF3- Sick'}}
2018-04-22 07:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'ACT': 14.0, 'OT-SL': 10.0}
2018-04-22 17:00:00
{'scheduled': 48.0, 'reg_hours': 34.0, 'AC

{'scheduled': 48.0, 'reg_hours': 48.0}
2018-06-02 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2018-06-02 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2018-06-03 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2018-06-03 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2018-06-04 07:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
2018-06-04 17:00:00
{'scheduled': 48.0, 'reg_hours': 48.0}
DFF4
2018-05-28 07:00:00
{'type': 'scheduled'}
2018-05-28 07:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2018-05-28 17:00:00
{'scheduled': 10.0, 'reg_hours': 10.0}
2018-05-29 07:00:00
{'type': 'scheduled'}
2018-05-29 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2018-05-29 17:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2018-05-30 07:00:00
{'scheduled': 20.0, 'reg_hours': 20.0}
2018-05-30 17:00:00
{'type': 'scheduled'}
2018-05-30 17:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2018-05-31 07:00:00
{'scheduled': 34.0, 'reg_hours': 34.0}
2018-05-31 17:00:00
{'type': 'scheduled'}
2018-05-31 17:00:00
{

1

In [56]:
def add_hours(ts,token,typ):
    hours = 0.0
    try:
        if (shifts[token]['shifts'][shift]['acct']['type'] == typ):
            hours = shifts[token]['shifts'][shift]['acct']['hours']
    except TypeError:
        ;
    except KeyError:
        ;
    if (token == 'AOF1'):
        print(ts)
        print(typ)
        print(hours)
    return(hours)
            

In [44]:
hours = {}
hours['ff'] = []
hours['platoon'] = []
hours['cycle_start'] = []
hours['sl_hours'] = []
hours['swap_hours'] = []
hours['vc_hours'] = []
hours['iod_hours'] = []
hours['reg_hours'] = []
hours['prs_hours'] = []
hours['ber_hours'] = []
hours['act_hours'] = []
hours['cmpu_hours'] =[]

for platoon in ['A','B','C','D']:
    for ffn in ['OF1','OF2','OF3','OF4','FF1','FF2','FF3','FF4','FF5']:
        token = platoon+ ffn
        for shift in cycle_start[platoon]:
            hours['ff'].append(token)
            hours['platoon'].append(platoon)
            hours['cycle_start'].append(shift)
            sl_hours = 0.0
            ot_hours = 0.0
            swap_hours = 0.0
            vc_hours = 0.0
            iod_hours = 0.0
            reg_hours = 0.0
            prs_hours = 0.0
            ber_hours = 0.0
            act_hours = 0.0
            cmpu_hours = 0.0
            ts_list = []
            ts = shift
            ts_list.append(ts)
            ts += datetime.timedelta(days=1)
            ts_list.append(ts)
            ts += datetime.timedelta(days=1)
            ts += datetime.timedelta(hours=10)   # increment cycle start by 10 hours + 1 day
            ts_list.append(ts)
            ts += datetime.timedelta(days=1)
            ts_list.append(ts)
            
            for ts in ts_list:
                if (ts.hour == 7): shift_hours = 10.0
                if (ts.hour == 17): shift_hours = 14.0
                if ('acct' in shifts[token]['shifts'][ts]): 
#                    print(shifts[token]['shifts'][shift]['acct'])
                    vc_hours += add_hours(ts,token,'VC')
                    swap_hours += add_hours(ts,token,'SWAP')
                    iod_hours += add_hours(ts,token,'IOD')
                    sl_hours += add_hours(ts,token,'SL')
                    prs_hours += add_hours(ts,token,'PRS')
                    ber_hours += add_hours(ts,token,'BER')
                    act_hours += add_hours(ts,token,'ACT')
                    cmpu_hours += add_hours(ts,token,'CMP-U')
                else:
                    reg_hours += shift_hours
            hours['sl_hours'].append(sl_hours)
            hours['swap_hours'].append(swap_hours)
            hours['vc_hours'].append(vc_hours)
            hours['iod_hours'].append(iod_hours)
            hours['reg_hours'].append(reg_hours)
            hours['prs_hours'].append(prs_hours)
            hours['ber_hours'].append(ber_hours)
            hours['act_hours'].append(act_hours)
            hours['cmpu_hours'].append(cmpu_hours)
                
            
            
hourspd = pd.DataFrame(hours)
hourspd
#hourspd.groupby(hourspd['ff']).sum()

2017-01-04 07:00:00
VC
0.0
2017-01-04 07:00:00
SWAP
0.0
2017-01-04 07:00:00
IOD
0.0
2017-01-04 07:00:00
SL
0.0
2017-01-04 07:00:00
PRS
0.0
2017-01-04 07:00:00
BER
0.0
2017-01-04 07:00:00
ACT
0.0
2017-01-04 07:00:00
CMP-U
0.0
2017-01-05 17:00:00
VC
0.0
2017-01-05 17:00:00
SWAP
0.0
2017-01-05 17:00:00
IOD
0.0
2017-01-05 17:00:00
SL
0.0
2017-01-05 17:00:00
PRS
0.0
2017-01-05 17:00:00
BER
0.0
2017-01-05 17:00:00
ACT
0.0
2017-01-05 17:00:00
CMP-U
0.0
2017-01-06 17:00:00
VC
0.0
2017-01-06 17:00:00
SWAP
0.0
2017-01-06 17:00:00
IOD
0.0
2017-01-06 17:00:00
SL
0.0
2017-01-06 17:00:00
PRS
0.0
2017-01-06 17:00:00
BER
0.0
2017-01-06 17:00:00
ACT
0.0
2017-01-06 17:00:00
CMP-U
0.0
2017-01-11 07:00:00
VC
0.0
2017-01-11 07:00:00
SWAP
0.0
2017-01-11 07:00:00
IOD
0.0
2017-01-11 07:00:00
SL
10.0
2017-01-11 07:00:00
PRS
0.0
2017-01-11 07:00:00
BER
0.0
2017-01-11 07:00:00
ACT
0.0
2017-01-11 07:00:00
CMP-U
0.0
2017-03-03 17:00:00
VC
0.0
2017-03-03 17:00:00
SWAP
0.0
2017-03-03 17:00:00
IOD
0.0
2017-03-03 17:0

ff platoon         cycle_start  sl_hours  swap_hours  vc_hours  \
0     AOF1       A 2016-12-26 07:00:00       0.0         0.0       0.0   
1     AOF1       A 2017-01-03 07:00:00       0.0         0.0       0.0   
2     AOF1       A 2017-01-11 07:00:00      10.0         0.0       0.0   
3     AOF1       A 2017-01-19 07:00:00       0.0         0.0       0.0   
4     AOF1       A 2017-01-27 07:00:00       0.0         0.0       0.0   
5     AOF1       A 2017-02-04 07:00:00       0.0         0.0       0.0   
6     AOF1       A 2017-02-12 07:00:00       0.0         0.0       0.0   
7     AOF1       A 2017-02-20 07:00:00       0.0         0.0       0.0   
8     AOF1       A 2017-02-28 07:00:00       0.0         0.0       0.0   
9     AOF1       A 2017-03-08 07:00:00       0.0         0.0       0.0   
10    AOF1       A 2017-03-16 07:00:00       0.0         0.0       0.0   
11    AOF1       A 2017-03-24 07:00:00       0.0         0.0       0.0   
12    AOF1       A 2017-04-01 07:00:00       0.0         0.0       0.0   
13    AOF1       A 2017-04-09 07:00:00       0.0         0.0       0.0   
14    AOF1       A 2017-04-17 07:00:00       0.0         0.0      40.0   
15    AOF1       A 2017-04-25 07:00:00       0.0         0.0       0.0   
16    AOF1       A 2017-05-03 07:00:00       0.0         0.0       0.0   
17    AOF1       A 2017-05-11 07:00:00       0.0         0.0       0.0   
18    AOF1       A 2017-05-19 07:00:00       0.0         0.0       0.0   
19    AOF1       A 2017-05-27 07:00:00       0.0         0.0       0.0   
20    AOF1       A 2017-06-04 07:00:00       0.0         0.0       0.0   
21    AOF1       A 2017-06-12 07:00:00       0.0         0.0       0.0   
22    AOF1       A 2017-06-20 07:00:00       0.0         0.0       0.0   
23    AOF1       A 2017-06-28 07:00:00       0.0         0.0       0.0   
24    AOF1       A 2017-07-06 07:00:00       0.0         0.0       0.0   
25    AOF1       A 2017-07-14 07:00:00       0.0         0.0       0.0   
26    AOF1       A 2017-07-22 07:00:00       0.0         0.0       0.0   
27    AOF1       A 2017-07-30 07:00:00       0.0         0.0       0.0   
28    AOF1       A 2017-08-07 07:00:00       0.0         0.0       0.0   
29    AOF1       A 2017-08-15 07:00:00       0.0         0.0       0.0   
30    AOF1       A 2017-08-23 07:00:00       0.0         0.0       0.0   
31    AOF1       A 2017-08-31 07:00:00       0.0         0.0       0.0   
32    AOF1       A 2017-09-08 07:00:00       0.0         0.0       0.0   
33    AOF1       A 2017-09-16 07:00:00       0.0         0.0       0.0   
34    AOF1       A 2017-09-24 07:00:00       0.0         0.0       0.0   
35    AOF1       A 2017-10-02 07:00:00       0.0        40.0       0.0   
36    AOF1       A 2017-10-10 07:00:00       0.0         0.0       0.0   
37    AOF1       A 2017-10-18 07:00:00       0.0         0.0       0.0   
38    AOF1       A 2017-10-26 07:00:00       0.0         0.0       0.0   
39    AOF1       A 2017-11-03 07:00:00       0.0         0.0       0.0   
40    AOF1       A 2017-11-11 07:00:00       0.0         0.0       0.0   
41    AOF1       A 2017-11-19 07:00:00       0.0         0.0       0.0   
42    AOF1       A 2017-11-27 07:00:00       0.0         0.0       0.0   
43    AOF1       A 2017-12-05 07:00:00       0.0         0.0       0.0   
44    AOF1       A 2017-12-13 07:00:00       0.0         0.0       0.0   
45    AOF1       A 2017-12-21 07:00:00       0.0         0.0       0.0   
46    AOF1       A 2017-12-29 07:00:00       0.0         0.0       0.0   
47    AOF1       A 2018-01-06 07:00:00       0.0         0.0       0.0   
48    AOF1       A 2018-01-14 07:00:00       0.0         0.0       0.0   
49    AOF1       A 2018-01-22 07:00:00       0.0         0.0       0.0   
50    AOF1       A 2018-01-30 07:00:00       0.0         0.0       0.0   
51    AOF1       A 2018-02-07 07:00:00       0.0         0.0       0.0   
52    AOF1       A 2018-02-15 07:00:00       0.0         0.0       0.0   
53    AOF1  

In [25]:
for token in shifts.keys():
    print(token_FF[token])
    for shift in shifts[token]:
        try:
            typ = shifts[token]['shifts'][shift]['acct']['type']
            if typ in ['VC','SL','PER','IOD']:
                print(str(shift) + ' ' + typ)
                for ff_covering in shifts.keys():
                    try:
                        for_ff = shifts[ff_covering]['shifts'][shift]['acct']['for_ff']
                        if (for_ff == ff_name):
                            print(str(shift)+ ' ' + ff_covering + ' covering for: ' + for_ff )
                    except KeyError:
                        continue
        except KeyError:
            continue

Lt Richardson
Lt Bailey
Capt Montville
Lt Monaghan
FF Archambault
FF O'Donnell
Prob-FF Preston
FF Campbell
FF DeLuca
Lt Perry
Lt Gardner
Lt Beaudreau
Lt Grady
FF Columbier
FF Snowling
FF Howard
Prob-FF Crute
Prob-FF Perry
Capt Mears
Lt Jones
Lt Purcell
Lt Greene
FF King
FF Andrade
FF Szerlag
FF Forte
FF McKeon
Lt Hall
Lt Babcock
Lt Warner III
Lt Matola, Jr.
FF Marsh
FF Stabile
FF Lang Jr.
Prob-FF Lavallee
Prob-FF Gorman


In [25]:
for token in shifts.keys():
    print(token_FF[token])
    for shift in shifts[token]:
        try:
            typ = shifts[token]['shifts'][shift]['acct']['type']
            if typ in ['VC','SL','PER','IOD']:
                print(str(shift) + ' ' + typ)
                for ff_covering in shifts.keys():
                    try:
                        for_ff = shifts[ff_covering]['shifts'][shift]['acct']['for_ff']
                        if (for_ff == ff_name):
                            print(str(shift)+ ' ' + ff_covering + ' covering for: ' + for_ff )
                    except KeyError:
                        continue
        except KeyError:
            continue

Lt Richardson
Lt Bailey
Capt Montville
Lt Monaghan
FF Archambault
FF O'Donnell
Prob-FF Preston
FF Campbell
FF DeLuca
Lt Perry
Lt Gardner
Lt Beaudreau
Lt Grady
FF Columbier
FF Snowling
FF Howard
Prob-FF Crute
Prob-FF Perry
Capt Mears
Lt Jones
Lt Purcell
Lt Greene
FF King
FF Andrade
FF Szerlag
FF Forte
FF McKeon
Lt Hall
Lt Babcock
Lt Warner III
Lt Matola, Jr.
FF Marsh
FF Stabile
FF Lang Jr.
Prob-FF Lavallee
Prob-FF Gorman


In [27]:
counts = {}

for token in shifts:
    for shift in shifts[token]['shifts']:
        try:
            typ = shifts[token]['shifts'][shift]['acct']['type']
            if (typ == 'GT'): print(token_FF[token])
            if (typ in counts.keys()):
                counts[typ] += 1
            else:
                counts[typ] = 1
        except KeyError:
            ;

In [28]:
counts

{'SWAP': 445,
 'VC': 679,
 'SL': 432,
 'PRS': 78,
 'OT-VC': 618,
 'OT-PRS': 71,
 'OT-BERV': 23,
 'OT-SL': 365,
 'SWAPW': 441,
 'OT': 428,
 'DP': 48,
 'OT-ADM': 64,
 'OT-BARG': 15,
 'OT-IOD': 545,
 'OT-COMP': 62,
 'CS-APP': 7,
 'C-DD': 365,
 'CS-SO': 12,
 'C-ND': 325,
 'OT-EOD': 6,
 'IOD': 858,
 'CMP-U': 75,
 'ADMIN': 73,
 'CS-TRN': 14,
 'CMP-E': 76,
 'CT': 2,
 'C-FP': 8,
 'C-TRN': 5,
 'OFF': 1,
 'BER': 37,
 'ACTOT': 9,
 'SCH': 3,
 'C-DIVE': 14,
 'BARG': 16,
 'OT-VNCY': 64,
 'ACT': 68,
 'CS-EMS': 101,
 'UT': 2,
 'CS-FP': 2,
 'CS-FA': 122,
 'CS-SCBA': 7,
 'OT-SCH': 3,
 'C-BM': 15,
 'DFP': 8,
 'OT-EMERG': 2,
 'C-APP': 1,
 'EMER': 1}

## Check for situation of alleged 'gaming' OT and VAC

Scenario:  FF1 takes a vacation day, FF2 gets OT for covering FF1's vacation day
           Later in FF1's 8 day cycle, FF2 takes a vacation day and FF1 gets OT for covering it.
           
Algorithm: 

            For each FF, look at 8-day cycles in which he took a vacation day (or other day requiring coverage).  

            See if, in this 8-day cycle, this FF was paid for covering a day taken by the FF who covered his. 

In [ ]:
 match_count = 0

for ff_name in shifts.keys():                          # loop through FF list
    platoon = FF_platoon[ff_name]                      # get the platoon (A,B,C,D) for this FF
    ff_id = FF_ID[ff_name]                             # get page number
    print('Processing ' + ff_name + ' ' + str(ff_id) + ' ' + platoon)           # display name and id #
    for first_shift in cycle_start[platoon]:           # loop through shift start times that begin an 8-day cycle
        cycle_shifts = []                              # fill in the other shift start times for that cycle
        ts = first_shift
        for day in range(1,9):
            cycle_shifts.append(ts)
            ts += datetime.timedelta(hours=10)          
            cycle_shifts.append(ts)
            ts += datetime.timedelta(hours=14)
        for ts in cycle_shifts:                                      # loop through the shifts for this 8-day cycle
            try:
                stype = shifts[ff_name][ts]['acct']['type']          # get accountability log entry if there is one
                if (stype in ['VC','SL','PRS','ADM','BER','ACT']):   # see if coverage may be required
                    print(ff_name + ' ' + str(ts) + ' ' + stype)    
                    for ff_cover in shifts.keys():                   # see who covered this shift
                        if (ff_cover != 'ff_name'):
                            try:
                                if (shifts[ff_cover][ts]['acct']['for_id'] == ff_id):
                                    print('covered by: ' + ff_cover )
                                    cover_id = FF_ID[ff_cover]
                                    for cs in cycle_shifts:          # see if the ff who covered was himself covered
                                        try:                         # by the ff we are processing in this cycle
                                            if (shifts[ff_name][cs]['acct']['for_id'] == cover_id):
                                                typ = shifts[ff_name][cs]['acct']['type']
                                                print('match########## ' + str(cs) + ' ' + ff_name + ' for ' + ff_cover + ' ' + typ)
                                                if ('SWAP' not in typ): match_count += 1
                                        except KeyError:
                                            continue
                            except KeyError:
                                continue
            except KeyError:
                continue                                             #get here if no accountability log
                                
print(match_count)        

In [ ]:
def ptabl(platoon,ts,shifts,file):        
    file.write('<tr><td>' + str(ts) + '</td><td>' + platoon + '</td>')
    for i in range(1,5):
        ff_desig = 'OF' + platoon + str(i)
        ff_name = desig_FF[ff_desig]
        ff_cover = chk_cov(ff_name,ts)
        tag = ff_desig + str(ts)
        tds =('<td>')
        try:
            typ = shifts[ff_name]['shifts'][ts]['acct']['type']
            if (typ == 'IOD'):                      # set background purple for IOD
                tds = '<td bgcolor="#FF00FF">'
            if (typ == 'SL'):                       # set background gray for SL
                tds = '<td bgcolor="#C0C0C0">'
            if (typ == 'VC'):                       # set background light blue for VC
                tds = '<td bgcolor="#00FFFF">'
            if ((typ == 'PRS') | (typ == 'BER')):   # set background yellow for personal and bereavement 
                tds = '<td bgcolor="#FFFF00">'
            file.write(tds + '<a href="#' + tag + '">' + typ + '</a>')
        except KeyError:
            file.write(tds + 'On')
        if (len(ff_cover) > 2):
            cover_tag = FF_desig[ff_cover] + str(ts)
            file.write('<br><a href="#' + cover_tag + '">' + ff_cover + '</a>')
        file.write('</td>')
    for i in range(1,6):
        ff_desig = 'FF' + platoon + str(i)
        ff_name = desig_FF[ff_desig]
        ff_cover = chk_cov(ff_name,ts)
        tds =('<td>')
        try:
            typ = shifts[ff_name]['shifts'][ts]['acct']['type']
            tag = ff_desig + str(ts)
            if (typ == 'IOD'):                      # set background purple for IOD
                tds = '<td bgcolor="#FF00FF">'
            if (typ == 'SL'):                       # set background gray for SL
                tds = '<td bgcolor="#C0C0C0">'
            if (typ == 'VC'):                       # set background light blue for VC
                tds = '<td bgcolor="#00FFFF">'
            if ((typ == 'PRS') | (typ == 'BER')):   # set background yellow for personal and bereavement 
                tds = '<td bgcolor="#FFFF00">'
            file.write(tds + '<a href="#' + tag + '">' + typ + '</a>')
        except KeyError:
            if ((ff_name == 'Prob-FF Preston') & (ts < datetime.datetime(2017,6,1,0,0,0))):
                file.write(tds + 'NA')
            else:
                file.write(tds + 'On')
        if (len(ff_cover) > 2):
            cover_tag = FF_desig[ff_cover] + str(ts)
            file.write('<br><a href="#' + cover_tag + '">' + ff_cover + '</a>')
        file.write('</td>')
    file.write('</tr>\n')
    return()

In [ ]:
file = open('../platoons.html','w') 

file.write('<html><body>') 

for platoon in ['A','B','C','D']:
    file.write('<h2>Platoon: ' + platoon + '</h2></a>\n')
    file.write('<table border="1">\n')
    file.write('<tr><td>&nbsp;</td><td>&nbsp;</td>')
    for i in range(1,5):
        file.write('<td>OF' + platoon + str(i) + '</td>')
    for i in range(1,6):
        file.write('<td>FF' + platoon + str(i) + '</td>')
    file.write('</tr>\n')
    file.write('<tr><td>Shift</td><td>P</td>')
    for i in range(1,5):
        des = 'OF' + platoon + str(i)
        file.write('<td>'+ desig_FF[des] + '</td>')
    for i in range(1,6):
        des = 'FF' + platoon + str(i)
        file.write('<td>' + desig_FF[des]+ '</td>')
    file.write('</tr>\n')
        
    for ts in cycle_start[platoon]:
        if (ts < datetime.datetime(2018,5,21,1,0,0)):
            ts2 = ts
            ptabl(platoon,ts2,shifts,file)
            ts2 += datetime.timedelta(days=1)   #increment shift start by 1 day
            ptabl(platoon,ts2,shifts,file)
            ts2 += datetime.timedelta(days=1)   #increment shift start by 1 day
            ts2 += datetime.timedelta(hours=10)   #increment shift start 10 hours
            ptabl(platoon,ts2,shifts,file)
            ts2 += datetime.timedelta(days=1)   #increment shift start by 1 day
            ptabl(platoon,ts2,shifts,file)
    file.write('</table>\n')

acct_webpage(file,shifts)          #write webpage of accountability data with links

file.close() 

In [28]:
file = open('../summary.html','w') 

file.write('<html><body>') 

file.write('<table border="1" sidth="80%">')

for platoon in cycle_start.keys():
    for cs in cycle_start[platoon].keys():
        file.write('<tr><td>')
        file.write('<table border="1" width="100%"><tr><td>Platoon</td><td>Cycle Start</td></tr>')
        file.write('<tr><td>' + platoon + '</td><td>' + str(cs) + '</td></tr></table>\n')
        full_cycle = this_cycle(cs)
        print(cs)
        print('new cycle***********************************')
        file.write('<table border="1" width="100%">')
        file.write('<tr><td>FF</td><td>Regular</td><td>VC</td><td>SL</td><td>IOD</td><td>CD</td><td>OT</td></tr>')
        for ffn in ['OF1','OF2','OF3','OF4','FF1','FF2','FF3','FF4','FF5']:
            token = platoon+ ffn
            print(token)
            reg_hours = 0.0
            ts_list = this_cycle(cs)
            for ts in ts_list:
                sf = shift_hours(token,ts,shifts) 
                if (len(sf) == 1):
                    if ('scheduled' in sf.keys()): reg_hours += sf['scheduled'] 
            file.write('<tr><td>' + token + '</td>')
            file.write('<td>' + str(reg_hours) + '</td><td>&nbsp;</td><td>&nbsp;</td><td>&nbsp;</td><td>&nbsp;</td></tr>\n')
        file.write('</table></td></tr>')
    file.write('</table>')
        

2016-12-26 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-01-03 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-01-11 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-01-19 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-01-27 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-02-04 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-02-12 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-02-20 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-02-28 07:00:00
new cycle***********************************
AOF1
AOF2
AOF3
AOF4
AFF1
AFF2
AFF3
AFF4
AFF5
2017-03-08

BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-02-17 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-02-25 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-03-05 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-03-13 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-03-21 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-03-29 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-04-06 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-04-14 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1
BFF2
BFF3
BFF4
BFF5
2018-04-22 07:00:00
new cycle***********************************
BOF1
BOF2
BOF3
BOF4
BFF1


DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-02-10 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-02-18 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-02-26 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-03-06 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-03-14 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-03-22 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-03-30 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-04-07 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4
DFF1
DFF2
DFF3
DFF4
DFF5
2017-04-15 07:00:00
new cycle***********************************
DOF1
DOF2
DOF3
DOF4


In [27]:
shifts

{'AOF1': {'name': 'Lt Richardson',
  'platoon': 'A',
  'shifts': {datetime.datetime(2016, 12, 26, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2016, 12, 27, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2016, 12, 28, 17, 0): {'type': 'scheduled'},
   datetime.datetime(2016, 12, 29, 17, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 3, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 4, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 5, 17, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 6, 17, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 11, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 12, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 13, 17, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 14, 17, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 19, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 20, 7, 0): {'type': 'scheduled'},
   datetime.datetime(2017, 1, 21, 1

In [70]:
counts = {}
hours = {}
scheduled = 0.0

for token in shifts.keys():
    for shift in shifts[token]['shifts']:
        if ((shift > datetime.datetime(2017,5,31,23,0,0)) & (shift < datetime.datetime(2018,5,25,1,0,0))):
            try:
                hrs = full_shift(shift)
                if (shifts[token]['shifts'][shift]['type'] == 'scheduled'): scheduled += hrs
            except KeyError:
                ;
            try:
                typ = shifts[token]['shifts'][shift]['acct']['type']
                if (typ in counts.keys()):
                    counts[typ] += 1
                    hours[typ] += shifts[token]['shifts'][shift]['acct']['hours']
                else:
                    counts[typ] = 1
                    hours[typ] = shifts[token]['shifts'][shift]['acct']['hours']
            except KeyError:
                ;

In [73]:
print(scheduled)
hours

77328.0


{'VC': 6192.0,
 'SWAP': 3650.0,
 'PRS': 800.0,
 'SL': 4134.0,
 'DP': 187.0,
 'OT': 850.5,
 'SWAPW': 3474.5,
 'OT-VC': 5657.0,
 'OT-SL': 3458.5,
 'OT-BARG': 66.0,
 'OT-IOD': 5939.75,
 'OT-PRS': 722.0,
 'OT-COMP': 454.0,
 'CS-APP': 13.0,
 'C-ND': 2887.0,
 'CS-SO': 29.5,
 'C-DD': 2412.0,
 'OT-ADM': 361.0,
 'OT-EOD': 84.0,
 'ADMIN': 528.0,
 'CMP-U': 530.0,
 'CS-TRN': 43.0,
 'CMP-E': 368.5,
 'OT-BERV': 198.0,
 'CT': 1.0,
 'C-FP': 21.5,
 'C-TRN': 17.0,
 'BER': 274.0,
 'SCH': 26.0,
 'C-DIVE': 54.0,
 'BARG': 69.0,
 'OT-VNCY': 399.0,
 'IOD': 8860.75,
 'CS-EMS': 263.5,
 'UT': 2.0,
 'ACT': 690.5,
 'CS-SCBA': 16.0,
 'ACTOT': 61.5,
 'OT-SCH': 26.0,
 'DFP': 31.5,
 'CS-FA': 223.5,
 'EMER': 8.0}